The short piece of code below implements a simulation of a wave packet being scattered at a potential barrier in one dimension.

You can download the code as an ipython notebook by clicking on the "Source" link above.

You can also run the simulation directly in your browser. Click button to start.

In [ ]:
# This cell has `interactive-button` as a tag in its metadata. 
# On export to HTML, it will be replaced by a button which loads the interactive runtime.

In [4]:
import numpy as np

# lattice laplace operator
def laplace(n):
  row = np.array( [-2,1] + [0]*(n-3) + [1] )
  return( np.array( [np.roll(row, k) for k in range(n)] ) )
    
# wave packet centered at mu, variance s, wave number k
def wavePacket(mu,s,k,n):
    return np.array( [np.exp(-(x-mu)**2/(2*s) + 1.0j*k*x) for x in range(n)] )

# space and time grid dimensions
n  = 700
nt = 450

# initial state
psi0 = wavePacket(n/3, n/10, 1, n)

# animate dynamics given potential barrier height v and width w
def create_animation(v,w):
    
    # build Hamiltonian
    # hbar = m = 1
    V = [v if (n/2<=x and x <=n/2+w) else 0 for x in range(n)]
    H = -laplace(n)/2 + np.diag(V)

    # diagonalize
    eigenvalues, basis = np.linalg.eigh(H);

    # expand initial state in eigenbasis
    coeffs = basis.conj().T@psi0;

    # create time evolution
    e_to_the_minus_i_eigs = np.exp(-1.0j*eigenvalues);
    return( [abs(basis@( (e_to_the_minus_i_eigs**t) * coeffs))**2 for t in range(nt)] )

### This cell won't be exported to HTML

$\hbar = m = a =1 \Rightarrow K = 1/2$

In [ ]:
import panel as pn
pn.extension()
from bokeh.plotting import figure, show
from bokeh.layouts import column
from bokeh.models import ColumnDataSource, Slider, Button, Styles

x = np.linspace(0, 1, n)
max_height = 2
max_width  = 30

def update_parameters():
    global y, player

    v = vSlider.value
    w = wSlider.value
    
    source_barrier.data = dict(x=[1/2,1/2,1/2+w/nt,1/2+w/nt],y=[0,v/max_height,v/max_height,0])
    y = create_animation(v, w)
    
    player.value = 0 
    update_time()
    
def update_time():
    source.data = dict(x=x, y=y[player.value])

vSlider = pn.widgets.FloatSlider(name="barrier height", start=0, end=max_height, step=0.01, value=1, sizing_mode='stretch_width')
wSlider = pn.widgets.FloatSlider(name="barrier width", start=.01, end=max_width, step=0.01, value=.01, sizing_mode='stretch_width')
player = pn.widgets.Player(start=0, end=nt-1, step=1, value=1, 
                               loop_policy='loop', show_loop_controls=True,
                               interval=25, sizing_mode='stretch_width')

for w in [vSlider, wSlider]:
    w.param.watch(lambda e: update_parameters(), "value_throttled")
player.param.watch(lambda e: update_time(), 'value')

source = ColumnDataSource()
source_barrier = ColumnDataSource()
update_parameters()
fig = figure(y_range=(0, 1), x_range=(0, 1), sizing_mode='stretch_width')
fig.line('x', 'y', source=source_barrier, color="gray", line_width=2)
fig.line('x', 'y', source=source, line_width=2)
fig.grid.visible = False
bokeh_fig = pn.pane.Bokeh(fig)

pn.Column(bokeh_fig, vSlider, wSlider, player).servable(target="fig")